In [1]:
import numpy as np
import pandas as pd
# 导入我自定义的模块
import sys
sys.path.append("./code_libs")
import alpha_tools as at

Checking data_tools dependencies...
Checking numpy >= 1.20.3...
Find that numpy == 1.21.5...
Checking pandas >= 1.3.4...
Find that pandas == 1.3.5...
Checking bottleneck >= 1.3.4...
Find that bottleneck == 1.3.4...
Checking graphviz >= 0.20...
Find that graphviz == 0.20...
Checking scikit-learn >= 1.0.1...
Find that scikit-learn == 1.0.2...
Checking xlrd >= 2.0.1...
Find that xlrd == 2.0.1...
Checking psutil >= 5.8.0...
Find that psutil == 5.9.0...
Checking openpyxl >= 3.0.9...
Find that openpyxl == 3.0.9...
Checking xlsxwriter >= 3.0.3...
Find that xlsxwriter == 3.0.3...
Checking data_tools dependencies finished.
Checking tree_tools dependencies...
Checking numpy >= 1.20.3...
Find that numpy == 1.21.5...
Checking pandas >= 1.3.4...
Find that pandas == 1.3.5...
Checking bottleneck >= 1.3.4...
Find that bottleneck == 1.3.4...
Checking graphviz >= 0.20...
Find that graphviz == 0.20...
Checking scikit-learn >= 1.0.1...
Find that scikit-learn == 1.0.2...
Checking xlrd >= 2.0.1...
Find that

In [2]:
# 导入数据
df_ = pd.read_csv("application_record.csv")
df_response = pd.read_csv("credit_record.csv")

In [3]:
# 添加“年龄”变量
df_['Age'] = -(df_['DAYS_BIRTH']) // 365
# 定义标签
df_["target"] = df_["ID"].map(df_response.groupby("ID")["STATUS"].apply(
lambda x: 1 if ({"2", "3", "4", "5"} & set(x)) else 2 if ({"1"} & set(x)) else 0))
# 定义切片
df_['birth_year'] = df_["Age"].map(lambda x: str(2021 - x) + "0101")
df_data = df_[df_["target"].notnull()]
# 划分数据集
from sklearn.model_selection import train_test_split
df_train, df_test = train_test_split(
	df_data, test_size=0.3, stratify=df_data["target"], random_state=42)

In [4]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v1-lgb/v1-lgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    # 默认参数为lgb
    # model_type_path="lightgbm.sklearn.LGBMClassifier",
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Find that enable_multi is True and n_jobs not set, setting to 2 !
WARNING Auto setting lightgbm params...
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'n_jobs': 2, 'use_missing': True, 'zero_as_missing': False}
INFO Using fit params: {'sample_weight': None, 'feature_name': 'auto', 'categorical_feature': [4, 8, 9, 12, 13, 14, 15, 16]}
INFO Using variables: 17...
INFO Training LGBMClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.001742 secs
INFO [FIT_TRANSFORM] ['Age']: 0.000737 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.00079 secs
INFO [FIT_TRANSFORM] ['CNT_FAM_MEMBERS']: 0.000663 secs
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.018484 secs
INFO [FIT_

In [5]:
at.tt.__pattern__["model_module_path"]

('sklearn.tree',
 'sklearn.ensemble',
 'imblearn.ensemble',
 'lightgbm.sklearn',
 'lightgbm',
 'xgboost.sklearn',
 'xgboost',
 'catboost')

In [6]:
at.tt.__config__["global_model_parameter"]

{'max_depth': 3, 'n_estimators': 30}

In [7]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v1-lgb-more/v1-lgb-more.xlsx",
    # df_train, "./策略分析demo/v1-lgb/v1-lgb.xlsx", test_data=df_test,
    # 同时入参两个数据集：测试、全量
    test_data=[df_test, df_data], train_name="开发", test_names=["测试", "全量"],
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Find that enable_multi is True and n_jobs not set, setting to 2 !
WARNING Auto setting lightgbm params...
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'n_jobs': 2, 'use_missing': True, 'zero_as_missing': False}
INFO Using fit params: {'sample_weight': None, 'feature_name': 'auto', 'categorical_feature': [4, 8, 9, 12, 13, 14, 15, 16]}
INFO Using variables: 17...
INFO Training LGBMClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.000935 secs
INFO [FIT_TRANSFORM] ['Age']: 0.00117 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.001071 secs
INFO [FIT_TRANSFORM] ['CNT_FAM_MEMBERS']: 0.000991 secs
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.019692 secs
INFO [FIT_

In [8]:
discrete_cols = df_train.dtypes[df_train.dtypes == object].index.tolist()
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v2-lgb/v2-lgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    customized_variables=discrete_cols,
)

WARNING Find that recover_from_json is None and customized_variables is not empty, setting limit_var_num to inf !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Find that enable_multi is True and n_jobs not set, setting to 2 !
WARNING Auto setting lightgbm params...
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'n_jobs': 2, 'use_missing': True, 'zero_as_missing': False}
INFO Using fit params: {'sample_weight': None, 'feature_name': 'auto', 'categorical_feature': [0, 1, 2, 3, 4, 5, 6, 7]}
INFO Using variables: 8...
INFO Training LGBMClassifier...
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.019736 secs
INFO [FIT_TRANSFORM] ['FLAG_OWN_CAR']: 0.08788 secs
INFO [FIT_TRANSFORM] ['FLAG_OWN_REALTY']: 0.018347 secs
INF

In [9]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v3-xgb/v3-xgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    # 调整参数为xgb
    model_type_path="xgboost.sklearn.XGBClassifier",
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Auto setting xgboost params...
WARNING Setting model params: enable_categorical to True !
WARNING Find that enable_categorical is True, xgboost tree_method not found, setting to hist !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'enable_categorical': True, 'tree_method': 'hist'}
INFO Using variables: 17...
INFO Training XGBClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.001061 secs
INFO [FIT_TRANSFORM] ['Age']: 0.000559 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.000749 secs
INFO [FIT_TRANSFORM] ['CNT_FAM_MEMBERS']: 0.00067 secs
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.010726 secs
INFO [FIT_TRANSFORM] ['DAYS_EMPLOYED']: 0.000496 secs
INFO [FIT_TRANSFORM] ['FLAG_EMAIL']: 0.000672 secs
INFO [FIT_TRANSFORM] ['FLAG_MOBIL']: 0.000682 secs
INFO [FIT_TRANSFORM

In [10]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v4-xgb/v4-xgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    # 调整参数为xgb
    model_type_path="xgboost.sklearn.XGBClassifier",
    customized_parameter={
        "min_child_weight": int(df_train.index.size * 0.01)
    }
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Auto setting xgboost params...
WARNING Setting model params: enable_categorical to True !
WARNING Find that enable_categorical is True, xgboost tree_method not found, setting to hist !
INFO Using model params: {'min_child_weight': 255, 'max_depth': 3, 'n_estimators': 30, 'enable_categorical': True, 'tree_method': 'hist'}
INFO Using variables: 17...
INFO Training XGBClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.001051 secs
INFO [FIT_TRANSFORM] ['Age']: 0.000581 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.000577 secs
INFO [FIT_TRANSFORM] ['CNT_FAM_MEMBERS']: 0.000587 secs
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.011464 secs
INFO [FIT_TRANSFORM] ['DAYS_EMPLOYED']: 0.000608 secs
INFO [FIT_TRANSFORM] ['FLAG_EMAIL']: 0.000662 secs
INFO [FIT_TRANSFORM] ['FLAG_MOBIL']: 0.00055

In [11]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v5-lgb/v5-lgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    # 继承已有模型
    model_exists="./模型分析demo/v13-lgb/Model_v13-lgb_model.pkl"
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
INFO Loading ./模型分析demo/v13-lgb/Model_v13-lgb_model.pkl...
WARNING Find that model_exists is not None, setting customized_variables to ['AMT_INCOME_TOTAL', 'Age', 'CNT_CHILDREN', 'CNT_FAM_MEMBERS', 'CODE_GENDER', 'DAYS_BIRTH', 'DAYS_EMPLOYED', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'FLAG_PHONE', 'FLAG_WORK_PHONE', 'NAME_EDUCATION_TYPE', 'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'NAME_INCOME_TYPE', 'OCCUPATION_TYPE'] !
WARNING DAYS_BIRTH in model_exists & exclude_column, removing from exclude_column...
WARNING Setting format_time_edge to True !
INFO Getting tree: 0 rules...
INFO Getting tree: 1 rules...
INFO Getting tree: 3 rules...
INFO Getting tree: 2 rules...
INFO Getting tree: 4 rules...
INFO Getting tree: 5 rules...
INFO Getting tree: 6 rules...
INFO Getting tree: 7 rules...
INFO Getting tree: 8 rules...
INFO Getting tree: 9 rules.

In [12]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v6/v6.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target",
    split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    customized_rule=[
        "DAYS_EMPLOYED,>=|nan,-962 & NAME_FAMILY_STATUS,in|nan,('Civil marriage','Married') & DAYS_EMPLOYED,<,-430"
    ]
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Overwriting customized_variables when customized_rule is not None !
INFO root
INFO No.2 DAYS_EMPLOYED < -962.0
INFO No.1 DAYS_EMPLOYED >= -962.0
INFO No.4 NAME_FAMILY_STATUS not in (Civil marriage, Married)
INFO No.3 NAME_FAMILY_STATUS in (Civil marriage, Married)
INFO No.6 DAYS_EMPLOYED >= -430.0
INFO No.5 DAYS_EMPLOYED < -430.0
INFO Done.
INFO Getting train detail...
INFO Getting train summary...
INFO root
INFO No.2 DAYS_EMPLOYED < -962.0
INFO No.1 DAYS_EMPLOYED >= -962.0
INFO No.4 NAME_FAMILY_STATUS not in (Civil marriage, Married)
INFO No.3 NAME_FAMILY_STATUS in (Civil marriage, Married)
INFO No.6 DAYS_EMPLOYED >= -430.0
INFO No.5 DAYS_EMPLOYED < -430.0
INFO Done.
INFO Getting test detail...
INFO Getting test summary...
INFO Caching psi detail...
INFO root
INFO No.2 DAYS_EMPLOYE

In [13]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v7/v7.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target",
    split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    customized_rule=[
        "DAYS_EMPLOYED,>=|nan,-962 & NAME_FAMILY_STATUS,in|nan,('Civil marriage','Married') & DAYS_EMPLOYED,<,-430"
    ],
    customized_nodes_dict={
        "negative": {"0": [4, 5]}, "positive": {"0": [2, 6]}
    }
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Overwriting customized_variables when customized_rule is not None !
INFO root
INFO No.2 DAYS_EMPLOYED < -962.0
INFO No.1 DAYS_EMPLOYED >= -962.0
INFO No.4 NAME_FAMILY_STATUS not in (Civil marriage, Married)
INFO No.3 NAME_FAMILY_STATUS in (Civil marriage, Married)
INFO No.6 DAYS_EMPLOYED >= -430.0
INFO No.5 DAYS_EMPLOYED < -430.0
INFO Done.
INFO Getting train detail...
INFO Getting train summary...
INFO root
INFO No.2 DAYS_EMPLOYED < -962.0
INFO No.1 DAYS_EMPLOYED >= -962.0
INFO No.4 NAME_FAMILY_STATUS not in (Civil marriage, Married)
INFO No.3 NAME_FAMILY_STATUS in (Civil marriage, Married)
INFO No.6 DAYS_EMPLOYED >= -430.0
INFO No.5 DAYS_EMPLOYED < -430.0
INFO Done.
INFO Getting test detail...
INFO Getting test summary...
INFO Caching psi detail...
INFO root
INFO No.2 DAYS_EMPLOYE

In [14]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v8-lgb/v8-lgb.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "DAYS_BIRTH"],  # 多变量分析时，DAYS_BIRTH会干扰Age的分析
    add_info="ID",  # 主键添加
    node_info="Age",
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
WARNING Find that enable_multi is True and n_jobs not set, setting to 2 !
WARNING Auto setting lightgbm params...
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'n_jobs': 2, 'use_missing': True, 'zero_as_missing': False}
INFO Using fit params: {'sample_weight': None, 'feature_name': 'auto', 'categorical_feature': [3, 7, 8, 11, 12, 13, 14, 15]}
INFO Using variables: 16...
INFO Training LGBMClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.000924 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.000535 secs
INFO [FIT_TRANSFORM] ['CNT_FAM_MEMBERS']: 0.000576 secs
INFO [FIT_TRANSFORM] ['CODE_GENDER']: 0.080702 secs
INFO [FIT_TRANSFORM] ['DAYS_EMPLOYED']: 0.000633 secs

In [15]:
at.Analysis.tree_flow(
    df_train, "./策略分析demo/v1-rec/v1-rec.xlsx", test_data=df_test,
    recover_from_json="./策略分析demo/v1-lgb/Tree_v1-lgb.json"
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
INFO Output tree: 0 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Output tree: 1 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] train detail...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] train summary...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] train detail...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] train summary...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] test detail...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] test summary...
INFO Caching psi detail...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] test detail...
INFO Output tree: 2 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972

In [16]:
ori_name = "./策略分析demo/v1-lgb/v1-lgb.xlsx"
new_output = "./策略分析demo/vr-lgb/vr-lgb.xlsx"
at.Analysis.tree_flow(
    df_train, new_output,
    test_data=[df_test, df_data], train_name="开发", test_names=["测试", "全量"],
    recover_path=ori_name,
)

INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
INFO Output tree: 0 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Output tree: 1 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] train detail...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] train detail...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] train summary...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] train summary...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] test detail...
INFO Getting tree: 1 - birth_year | 3 | (-inf, 1972-01-01] test summary...
INFO Caching psi detail...
INFO Output tree: 2 - birth_year | 3 | (-inf, 1972-01-01] flow...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972-01-01] test detail...
INFO Getting tree: 0 - birth_year | 3 | (-inf, 1972

In [17]:
# 打包结果
at.dt.Api.zip_dir_files("./策略分析demo/vr-lgb.zip", "./策略分析demo/vr-lgb")

INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-全量.pdf...
INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-测试.pdf...
INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-测试.json...
INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-全量.xlsx...
INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-测试.xlsx...
INFO Saving ./策略分析demo/vr-lgb/Tree_vr-lgb-开发-全量.json...


In [18]:
help(at.Report.create_tree_report)

Help on function in module alpha_tools:

create_tree_report(new_excel_name, excel_path_list, excel_name_list, train_test_dir_cn=None)
    Usage:
    ---------
    create_tree_report(
        "xxx.xlsx", [
            "file1.xlsx", "file2.xlsx", ...
        ], [
            "filename1", "filename2", ...
        ], ["train_display_name", "test_display_name"]
    )
    ---------



In [19]:
at.Report.create_tree_report(
    "./策略分析demo/vt-策略对比/vt-策略对比.xlsx", [
        "./策略分析demo/v1-lgb/v1-lgb.xlsx", "./策略分析demo/v2-lgb/v2-lgb.xlsx",
        "./策略分析demo/v3-xgb/v3-xgb.xlsx", "./策略分析demo/v4-xgb/v4-xgb.xlsx",
    ], ["v1-lgb", "v2-lgb", "v3-xgb", "v4-xgb"]
)

INFO Loading ./策略分析demo/v1-lgb/Tree_v1-lgb.xlsx...
INFO Loading ./策略分析demo/v2-lgb/Tree_v2-lgb.xlsx...
INFO Loading ./策略分析demo/v3-xgb/Tree_v3-xgb.xlsx...
INFO Loading ./策略分析demo/v4-xgb/Tree_v4-xgb.xlsx...
INFO Creating books summary...
INFO Saving...
INFO Creating 模型评估-特征重要性-v1-lgb...
INFO Creating 模型评估-特征重要性-v2-lgb...
INFO Creating 模型评估-特征重要性-v3-xgb...
INFO Creating 模型评估-特征重要性-v4-xgb...
INFO Creating 规则评估-正向规则-汇总-v1-lgb...
INFO Creating 规则评估-正向规则-汇总-v2-lgb...
INFO Creating 规则评估-正向规则-汇总-v3-xgb...
INFO Creating 规则评估-正向规则-汇总-v4-xgb...
INFO Creating 规则评估-负向规则-汇总-v1-lgb...
INFO Creating 规则评估-负向规则-汇总-v2-lgb...
INFO Creating 规则评估-负向规则-汇总-v3-xgb...
INFO Creating 规则评估-负向规则-汇总-v4-xgb...
INFO Creating 规则评估-整体规则汇总-v1-lgb...
INFO Creating 规则评估-整体规则汇总-v2-lgb...
INFO Creating 规则评估-整体规则汇总-v3-xgb...
INFO Creating 规则评估-整体规则汇总-v4-xgb...
INFO Creating 模型评估-节点详情-开发-v1-lgb...
INFO Creating 模型评估-节点详情-开发-v2-lgb...
INFO Creating 模型评估-节点详情-开发-v3-xgb...
INFO Creating 模型评估-节点详情-开发-v4-xgb...
INFO Creating 模型评估-节点详

(['./策略分析demo/v1-lgb/v1-lgb.xlsx',
  './策略分析demo/v2-lgb/v2-lgb.xlsx',
  './策略分析demo/v3-xgb/v3-xgb.xlsx',
  './策略分析demo/v4-xgb/v4-xgb.xlsx'],
 ['v1-lgb', 'v2-lgb', 'v3-xgb', 'v4-xgb'],
 None,
 {})